TO DO:
- Use matplotlib widget to plot MO
- Use UHF to calculate MO of atoms and molecule and construct MO diagrams
- Yrite wrapers for PySCF orbital analysis

This module allows the students to 
- visualize and analyse atomic and molecular orbitals
- build molecular diagrams.
- Calculate IP and EA using Koopman´s approximation.
- Link MO to chemical bon theory.

## Imports

In [ ]:

import numpy as np
import matplotlib.pyplot as plt
from pyscf import gto, scf, lib
from IPython.display import Image 
import numpy
from matplotlib.widgets import Slider
import scipy.special
from scipy.special import sph_harm
import math
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.io as pio

pio.renderers.default = "notebook"

## Define Hydrogen-like orbitals

In [2]:
def hydrogen_wf(n, l, m, X, Y, Z):

    R = numpy.sqrt(X ** 2 + Y ** 2 + Z ** 2)

    Theta = numpy.arccos(Z / R)
    Phi = numpy.arctan2(Y, X)

    rho = 2. * R / n
    s_harm = sph_harm(m, l, Phi, Theta)
    l_poly = scipy.special.genlaguerre(n - l - 1, 2 * l + 1)(rho)

    prefactor = numpy.sqrt((2. / n) ** 3 * math.factorial(n - l - 1) / (2. * n * math.factorial(n + l)))
    wf = prefactor * numpy.exp(-rho / 2.) * rho ** l * s_harm * l_poly
    wf = numpy.nan_to_num(wf)

    return wf

## Plot functions

In [24]:
# plotly 3D

def plotly_AO(orb_func, n=2, l=1, m=0, dz=0.5, zmin=-15, zmax=15):
    
    x = numpy.arange(zmin, zmax, dz)
    y = numpy.arange(zmin, zmax, dz)
    z = numpy.arange(zmin, zmax, dz)
    X, Y, Z = numpy.meshgrid(x, y, z)

    data = orb_func(n, l, m, X, Y, Z)
    data = abs(data) ** 2

    fig= go.Figure(data=go.Isosurface(
        x=X.flatten(),
        y=Y.flatten(),
        z=Z.flatten(),
        value=data.flatten(),
        opacity=0.6,
        isomin=0.0001,
        isomax=np.max(data),
        surface_count=6,
        caps=dict(x_show=False, y_show=False)
        ))

    fig.update_layout(title='Hydrogen orbital n={}, l={}, m={}'.format(n,l,m), autosize=False,
                    width=500, height=500,
                    margin=dict(l=65, r=50, b=65, t=90))

    #x axis
    fig.update_xaxes(visible=False, showgrid=False, showticklabels=False)

    #y axis    
    fig.update_yaxes(visible=False, showgrid=False, showticklabels=False)


    fig.show()

def pyplot_AO(orb_func, n=2, l=1, m=0, dz=0.2, zmin=-10, zmax=10):
    # must be used with %matplotlib widget

    x = numpy.arange(zmin, zmax, dz)
    y = numpy.arange(zmin, zmax, dz)
    z = numpy.arange(zmin, zmax, dz)
    X, Y, Z = numpy.meshgrid(x, y, z)

    # Change these to change which orbital to plot
    n = 2
    l = 1
    m = 0

    data = orb_func(n, l, m, X, Y, Z)
    data = abs(data) ** 2

    R = numpy.sqrt(X ** 2 + Y ** 2 + Z ** 2)

    fig, ax = plt.subplots()
    plt.subplots_adjust(left=0.15, bottom=0.15)
    im = plt.imshow(data[int((0 - zmin) / dz), :, :], vmin=0, vmax=numpy.max(data), extent=[zmin, zmax, zmin, zmax])
    plt.colorbar()
    #sli = Slider(plt.axes([0.25, 0.025, 0.65, 0.03]), "Y", z[0], z[len(z) - 1], valinit=0)
    sli = Slider(plt.axes([0.25, 0.025, 0.65, 0.03]), "Y", -3, 3, valinit=0)
    ax.set_title(
        "Orbital xz Slice (y=" + str("%.2f" % sli.val) + "): n=" + str(n) + ", l=" + str(l) + ", m=" + str(m))


    def update(val):
        index = int((sli.val - zmin) / dz)
        im.set_data(data[index, :, :])
        ax.set_title(
            "Orbital xz Slice (y=" + str("%.2f" % sli.val) + "): n=" + str(n) + ", l=" + str(l) + ", m=" + str(m))


    sli.on_changed(update)
    plt.show()

def plotly_MO(mol, mo_coeff, lim=2, n=40):
    
    nx, ny, nz = n, n, n
    X = np.linspace(-lim, lim, nx)
    Z = np.linspace(-lim, lim, ny)
    Y = np.linspace(-lim, lim, nz)

    coords = lib.cartesian_prod([X, Y, Z])

    # Compute orbital values on coord
    ao = mol.eval_gto("GTOval", coords)
    orb_on_coord = np.dot(ao, mo_coeff)

    # convert to mesh grid
    mesh = np.meshgrid(X, Y, Z, indexing='ij')
    orb_on_grid = np.zeros((nx, ny, nz))
    for ix in range(nx):
        for iy in range(ny):
            orb_on_grid[ix, iy, :] = orb_on_coord[nz * ny * ix + iy * nz: nz * ny * ix + iy * nz + nz]

    fig= go.Figure(data=go.Isosurface(
        x=mesh[0].flatten(),
        y=mesh[1].flatten(),
        z=mesh[2].flatten(),
        value=orb_on_grid.flatten(),
        opacity=0.6,
        isomin=0.1,
        isomax=np.max(orb_on_grid),
        surface_count=6,
        caps=dict(x_show=False, y_show=False)
        ))

    fig.update_scenes(xaxis_visible=False, yaxis_visible=False,zaxis_visible=False )

    return fig

## HF calculation

In [3]:
# Build molecule
mol_CO = gto.M()
mol_CO.atom = '''
    C 0. 0. 0.
    O 0. 0. 1.147 
    '''
mol_CO.basis = '''aug-cc-pvdz'''
mol_CO.spin = 0
mol_CO.build()

In [15]:
# Analyse the mol_CO object
mol_CO.ao_labels()[:10]
mol_CO.bas_exp(0)
mol_CO.atom_nshells(0)
mol_CO.energy_nuc()

In [22]:
# Perform a HF calculation
mf = scf.RHF(mol_CO)
mf.run()
mo_coeff = mf.mo_coeff
mo_energy = mf.mo_energy
occ = mf.mo_occ

converged SCF energy = -112.752246843491


## Plot HF molecular orbitals

In [30]:

mo6_coeff = mo_coeff[:, 6]

fig = plotly_MO(mol_CO, mo6_coeff, lim=3)

fig.add_trace(go.Scatter3d(
    x=[0, 0],
    y=[0, 0], 
    z=[0, 1.147], 
    mode='markers+text', 
    marker=dict(
        size=[8,10],
        color=["black", "black"],
        opacity=1),
        text=["C", "O"],
        textposition="top center"
        )
    )


fig.update_layout(title='CO orbital', autosize=False,
                width=500, height=500)
                #margin=dict(l=65, r=50, b=65, t=90))

fig.show()